# Hyper parameter search for CQL

In [1]:
!pip install d3rlpy

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [3]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [4]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [5]:
dataset, states, actions, rewards = get_dataset([i+200 for  i in range(100)], path="collected_data/rl_stochpid.txt")

start
[ 0.00000000e+00  7.95731469e+08 -2.55189108e-01  2.54000047e-02
  2.57999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.30457556e-01 -3.26640595e-01  6.00000000e-01]
Read chunk # 201 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.22789108e-01 -1.71999953e-02
  2.39998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.18067885e-01 -4.36092621e-01  6.00000000e-01]
Read chunk # 202 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.89891077e-02  1.38000047e-02
  1.55999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -5.13215135e-01  3.00794900e-01]
Read chunk # 203 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  4.39310892e-01 -5.61999953e-02
 -4.10001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.81283783e-02  6.00000000e-01 -6.00000000e-01]
Read chunk # 204 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.02089108e-01  1.38000047e-02
  2.84999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.

[ 0.00000000e+00  7.95731469e+08 -4.29489108e-01  1.24000047e-02
  1.97999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.73149828e-01 -6.00000000e-01  6.00000000e-01]
Read chunk # 248 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  5.92108923e-02 -1.15999953e-02
 -2.20001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.12672481e-02  1.26197128e-01 -4.51488887e-01]
Read chunk # 249 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  2.47108923e-02  5.20000047e-02
  1.82999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.92298179e-01  4.75144083e-03 -9.25660004e-02]
Read chunk # 250 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.79989108e-01  2.20000469e-03
 -1.09000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -1.56992418e-01 -2.96852309e-01  6.00000000e-01]
Read chunk # 251 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.74189108e-01  3.20000469e-03
 -3.80001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.842066

start
[ 0.00000000e+00  7.95731469e+08 -3.41289108e-01  3.60000047e-02
 -1.40001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -8.27789575e-02 -6.00000000e-01  6.00000000e-01]
Read chunk # 296 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.38689108e-01 -5.93999953e-02
 -1.91000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -5.34781862e-01 -5.98562622e-01  6.00000000e-01]
Read chunk # 297 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -5.56891077e-02  5.34000047e-02
  5.39998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -8.88291560e-02 -4.76291386e-02  4.12724585e-01]
Read chunk # 298 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.17510892e-01 -3.65999953e-02
 -1.66000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.00240960e-01  2.90765602e-01 -6.00000000e-01]
Read chunk # 299 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.10289108e-01 -1.99995308e-04
  1.48999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  2.

In [6]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -116.6173,
 'std': 91.33919,
 'min': -391.5658,
 'max': 0.0,
 'histogram': (array([ 3,  2,  2,  1,  0,  2,  0,  3,  1,  2,  3,  3,  3,  5,  7, 16, 22,
         21,  3,  1]),
  array([-391.5658  , -371.98752 , -352.4092  , -332.83093 , -313.25262 ,
         -293.67435 , -274.09607 , -254.51776 , -234.93948 , -215.36119 ,
         -195.7829  , -176.2046  , -156.62631 , -137.04803 , -117.46974 ,
          -97.89145 ,  -78.313156,  -58.73487 ,  -39.156578,  -19.578289,
            0.      ], dtype=float32))}

In [7]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [8]:
from d3rlpy.algos import CQL
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [10]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = CQL(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
                actor_encoder_factory = actor_encoder,
                critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                temp_learning_rate=temp_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+1000 for i  in range(20)], 
                                                                    path="collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i for i in range(40)], 
                                                                    path="collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_cql.pkl", "wb") as f:
            print("most optimal hyper params for cql at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_cql.pt")
        model.save_policy("policy_hyperparams_cql.pt")


search iteration:  0
using hyper params:  [0.0036556078225843873, 0.006829098750049013, 2.7952188951653185e-05, 3]
2022-04-18 20:56.50 [debug    ] RoundIterator is selected.
2022-04-18 20:56.50 [info     ] Directory is created at d3rlpy_logs/CQL_20220418205650
2022-04-18 20:56.50 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-18 20:56.50 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-18 20:56.50 [warning  ] Skip building models since they're already built.
2022-04-18 20:56.50 [info     ] Parameters are saved to d3rlpy_logs/CQL_20220418205650/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'vector', 'params': {'hidden_units': [12, 24, 36, 24, 12], 'activation': 'relu', 'use_batch_norm': True, 'dropout_rate': 0.2, 'use_dense': False}}, 'actor_learning_rate': 0.0036556078225843873, 'actor_optim_factory': {'optim_cls': 'Adam', 'betas': 

Epoch 1/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-18 20:57.02 [info     ] CQL_20220418205650: epoch=1 step=342 epoch=1 metrics={'time_sample_batch': 0.00029188499116061025, 'time_algorithm_update': 0.03346241775311922, 'temp_loss': 4.913380146026611, 'temp': 0.9950274912237423, 'alpha_loss': -18.47138302228604, 'alpha': 1.0172374391416361, 'critic_loss': 52.48261268794188, 'actor_loss': 0.15674881589168693, 'time_step': 0.03381775276005616, 'td_error': 0.932056132827221, 'init_value': -2.826847553253174, 'ave_value': -1.8378041797540747} step=342
2022-04-18 20:57.02 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220418205650/model_342.pt


Epoch 2/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-18 20:57.14 [info     ] CQL_20220418205650: epoch=2 step=684 epoch=2 metrics={'time_sample_batch': 0.0003051067653455232, 'time_algorithm_update': 0.031092922589932268, 'temp_loss': 4.972192969238549, 'temp': 0.9854013761233168, 'alpha_loss': -18.29798436304282, 'alpha': 1.051860821525953, 'critic_loss': 90.9461386161938, 'actor_loss': 1.2658058389237052, 'time_step': 0.0314597797672651, 'td_error': 0.9383969419539996, 'init_value': -4.3361077308654785, 'ave_value': -2.687583249173723} step=684
2022-04-18 20:57.14 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220418205650/model_684.pt


...

2022-04-19 02:44.00 [info     ] FQE_20220419024327: epoch=49 step=17395 epoch=49 metrics={'time_sample_batch': 8.756274908361301e-05, 'time_algorithm_update': 0.0015774579115316902, 'loss': 0.60870492122018, 'time_step': 0.0016966356358058016, 'init_value': -22.71050453186035, 'ave_value': -35.09301730552389, 'soft_opc': nan} step=17395


2022-04-19 02:44.00 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220419024327/model_17395.pt


Epoch 50/50:   0%|          | 0/355 [00:00<?, ?it/s]

2022-04-19 02:44.00 [info     ] FQE_20220419024327: epoch=50 step=17750 epoch=50 metrics={'time_sample_batch': 8.632565887880998e-05, 'time_algorithm_update': 0.0015483547264421489, 'loss': 0.5985047781603857, 'time_step': 0.0016666862326608577, 'init_value': -22.515283584594727, 'ave_value': -34.75557185366961, 'soft_opc': nan} step=17750


2022-04-19 02:44.00 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220419024327/model_17750.pt


## Reading hyper params from file

In [11]:
with open("hyperparams_cql.pkl", "rb") as f:
    data = pkl.load(f)

print(data)

[0.003303648455992173, 0.009991964442347354, 1.0037952986397458e-05, 1]
